# Introduction: Problem

- Singapore has a large proportion of dual income families and parents often rely on childcare services to look after their children on weekdays.
- Generally there are shortage of childcare services. Parents typicall have to queue for months to get a slot
- Due to extremely high price of cars, the general population typically rely on public transport (MRT and Bus)
- Availability of childcare services and its proximity to public transport is an important factor to consider when deciding which neighborhoods to live in Singapore.
- Other amenities such as grocery stores, restaurants, and gyms is also an important factor

# Data

### Childcare services
Comprehensive childcare center data is hard to get from commercial sources like Foursquare or even Google. Luckily the Singapore government have this data publicly available at: https://data.gov.sg/dataset/listing-of-centres

### Neighborhood

Singapore has highly efficient public transportation system and also extremely high price of cars. As a result, the majority of population rely in public transport for their daily commute. MRT stations often serve as a hub for neighborhoods and many aspect of life and amenities are organized around this hub. When on think of "neighborhood" in Singapore, often the MRT station in that location come to mind.

Data for MRT station is not available in Foursquare. It is available in Google, but has an associated cost.The Singapore government made the list and location of all MRT stations publicly available at: www.data.gov.sg. It is also available at Kaggle at: https://www.kaggle.com/yxlee245/singapore-train-station-coordinates. We use the Kaggle data for simplicity.

### Other amenities
Other amenities data can be found easily in Foursquare and Google. While Foursquare data is unfortunately not comprehensive in Singapore, we use this source for cost reason.

## Import necessary libraries

In [1]:
import numpy as np
import pandas as pd
import json
import requests
from pandas.io.json import json_normalize

from geopy.geocoders import Nominatim
import geopy.distance

# Matplotlib and associated plotting modules
import matplotlib as mlp
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib.colors as colors
import folium

# import k-means from clustering stage
from sklearn.cluster import KMeans

## Import and process data for childcare services location


In [3]:
df = pd.read_csv('listing-of-centre.csv')
df

tp_code centre_code                                        centre_name  \
0         na      RC1640         KINDERYEARS CHILDCARE & DEVELOPMENT CENTRE   
1         na      PT6560                           LORNA WHISTON PRE-SCHOOL   
2         na      PT8690                           LORNA WHISTON PRE-SCHOOL   
3         na      PT9730                                Jessin Kindergarten   
4         na      PT9354                    DISCOVERY KIDZ EMPIRE PTE. LTD.   
...      ...         ...                                                ...   
1890  TP0245          na  PCF Sparkletots Preschool @ Queenstown Blk 78B...   
1891  TP0246          na                             MY World Preschool Ltd   
1892  TP0244          na                     Skool4kidz@Sembawang EastCreek   
1893  TP0243          na          PCF SPARLETOTS PRESCHOOL @ JOO CHIAT (DS)   
1894  TP0424          na                  Skool4Kidz Campus @ Fernvale Lane   

     organisation_code     organisation_description service_model  \
0                   RC  Not-for-Profit Organisation            CC   
1                   PT            Private Operators            CC   
2                   PT            Private Operators            CC   
3                   PT            Private Operators            KN   
4                   PT            Private Operators            CC   
...                ...                          ...           ...   
1890                PT            Private Operators           EYC   
1891                PT            Private Operators            CC   
1892                PT            Private Operators            CC   
1893                PT            Private Operators            DS   
1894                PT            Private Operators            CC   

     centre_contact_no             centre_email_address  \
0             81018174               ky_cck@hotmail.com   
1             68718782   winchester@lornawhiston.com.sg   
2             68718748  kallangwave@lornawhiston.com.sg   
3             94897277            jessica@jessin.edu.sg   
4             64668386    ZUBAIDAHMDHANIFFA@HOTMAIL.COM   
...                ...                              ...   
1890                na           Tan.Sow.Wah@pcf.org.sg   
1891                na           enquiry@myworld.org.sg   
1892                na        enquiry@Skool4kidz.com.sg   
1893                na               PMD.CMS@pcf.org.sg   
1894          62802272        enquiry@skool4kidz.com.sg   

                                         centre_address postal_code  ...  \
0             679,CHOA CHU KANG CRESCENT,#01-602,680679      680679  ...   
1                             09,WINCHESTER ROAD,117783      117783  ...   
2       1,STADIUM PLACE,#01-24,KALLANG WAVE MALL,397628      397628  ...   
3               blk 255 Bishan Street 22,#04-454,570255      570255  ...   
4               96,FARRER ROAD,CHIP HOCK GARDENS,259225      259225  ...   
...                                                 ...         ...  ...   
1890                78B,Strathmore Avenue,#02-01,143078      143078  ...   
1891  132,Canberra View,#03-01,Eastlink @ Canberra,7...      750132  ...   
1892                         101,Canberra Street,750101      750101  ...   
1893                     15,LORONG K TELOK KURAU,425611      425611  ...   
1894                           60,Sengkang West Avenue,          na  ...   

     spark_certified weekday_full_day     saturday             scheme_type  \
0                 No      07:00-19:00  07:00-14:00                      na   
1                 No      07:00-19:00  07:00-14:00                      na   
2                 No      07:00-19:00  07:00-14:00                      na   
3                 No      08:00-13:00           na                      na   
4                 No      07:00-19:00  07:00-14:00                      na   
...              ...              ...          ...                     ...   
1890              No      07:00-19:00  07:00-14:00  Anchor 

In [34]:
# Filter unneccessary row
# For this project we only need centre name and postal code, but I'm keeping other columns for future project

df1 = df.filter(items = ['centre_code','centre_name','centre_address','postal_code', 'infant_vacancy','pg_vacancy','n1_vacancy','n2_vacancy','k1_vacancy','k2_vacancy','food_offered','spark_certified','weekday_full_day','provision_of_transport','government_subsidy'])
df1['centre_address'] = df1['centre_address'].str.rsplit(',' , n=1, expand=True)
df1['centre_address'] = df1['centre_address'].str.replace(',' , ' ')
df1

centre_code                                        centre_name  \
0         RC1640         KINDERYEARS CHILDCARE & DEVELOPMENT CENTRE   
1         PT6560                           LORNA WHISTON PRE-SCHOOL   
2         PT8690                           LORNA WHISTON PRE-SCHOOL   
3         PT9730                                Jessin Kindergarten   
4         PT9354                    DISCOVERY KIDZ EMPIRE PTE. LTD.   
...          ...                                                ...   
1890          na  PCF Sparkletots Preschool @ Queenstown Blk 78B...   
1891          na                             MY World Preschool Ltd   
1892          na                     Skool4kidz@Sembawang EastCreek   
1893          na          PCF SPARLETOTS PRESCHOOL @ JOO CHIAT (DS)   
1894          na                  Skool4Kidz Campus @ Fernvale Lane   

                                    centre_address postal_code infant_vacancy  \
0               679 CHOA CHU KANG CRESCENT #01-602      680679             na   
1                               09 WINCHESTER ROAD      117783             na   
2         1 STADIUM PLACE #01-24 KALLANG WAVE MALL      397628             na   
3                 blk 255 Bishan Street 22 #04-454      570255             na   
4                 96 FARRER ROAD CHIP HOCK GARDENS      259225             na   
...                                            ...         ...            ...   
1890                  78B Strathmore Avenue #02-01      143078             na   
1891  132 Canberra View #03-01 Eastlink @ Canberra      750132             na   
1892                           101 Canberra Street      750101             na   
1893                       15 LORONG K TELOK KURAU      425611             na   
1894                       60 Sengkang West Avenue          na             na   

     pg_vacancy n1_vacancy n2_vacancy k1_vacancy k2_vacancy  \
0     Immediate  Immediate  Immediate  Immediate  Immediate   
1            na         na         na         na         na   
2            na         na         na         na         na   
3            na         na         na         na         na   
4            na         na         na         na         na   
...         ...        ...        ...        ...        ...   
1890         na         na         na         na         na   
1891         na         na         na         na         na   
1892         na         na         na         na         na   
1893         na         na         na         na         na   
1894         na         na         na         na         na   

                                           food_offered spark_certified  \
0     No Pork No Lard with No Beef (without Certific...              No   
1     No Pork No Lard with No Beef (without Certific...              No   
2     No Pork No Lard with No Beef (from Non-Halal S...              No   
3                                                    na              No   
4     No Pork No Lard with No Beef (without Certific...              No   
...                                                 ...             ...   
1890  No Pork No Lard with No Beef (without Certific...              No   
1891  No Pork No Lard with No Beef (without Certific...              No   
1892  No Pork No Lard with No Beef (from Non-Halal S...              No   
1893  No Pork No Lard with No Beef (without Certific...              No   
1894  No Pork No Lard with No Beef (without Certific...              No   

     weekday_full_day provision_of_transport government_subsidy  
0         07:00-19:00                     No                Yes  
1         07:00-19:00                    Yes                Yes  
2         07:00-19:00                     No                Yes  
3         08:00-13:00                    Yes                Yes  
4         07:00-19:00                    Yes                Yes  
...               ...                    ...                ...  
1890      07:00-19:00                     No               

In [29]:
# extract postal code data to get coordinate

postal_code = df1['postal_code']
postal_code

0       680679
1       117783
2       397628
3       570255
4       259225
         ...  
1890    143078
1891    750132
1892    750101
1893    425611
1894        na
Name: postal_code, Length: 1895, dtype: object

## Use Google Map API to get coordinate from postal code data

In [35]:
# load API key

with open('API_Key.json') as json_data:
    API_Key = json.load(json_data)

    Gmaps_Key = API_Key['Google_Maps_API_Key']
    FS_ID = API_Key['Foursquare_CLIENT_ID']
    FS_SECRET = API_Key['Foursquare_CLIENT_SECRET']

In [49]:
# To save quota, I ran the function to get coordinate data once and save it into a file. The code to get coordinate data is below.

"""
df1['lat'] = None
df1['lng'] = None
df1['neighborhood'] = None

for i in range(len(df1)):
    url = "https://maps.googleapis.com/maps/api/geocode/json?components=country:SG|postal_code:{}&key={}".format(postal_code[i],Gmaps_Key)
    results = requests.get(url).json()
    try:
        lat = results['results'][0]['geometry']['location']['lat']
        lng = results['results'][0]['geometry']['location']['lng']
        neighborhood = results['results'][0]['address_components'][1]['short_name']
        df1.loc[i, 'lat'] = lat
        df1.loc[i, 'lng'] = lng
        df1.loc[i, 'neighborhood'] = neighborhood
    except:
        lat = None
        lng = None
        neighborhood = None

df1.to_csv('childcare_sg_v2.csv',index=False)

"""

In [51]:
# Load file that contain coordinate data that I previously saved
df2 = pd.read_csv('childcare_sg_v2.csv')
df2

centre_code                                        centre_name  \
0         RC1640         KINDERYEARS CHILDCARE & DEVELOPMENT CENTRE   
1         PT6560                           LORNA WHISTON PRE-SCHOOL   
2         PT8690                           LORNA WHISTON PRE-SCHOOL   
3         PT9730                                Jessin Kindergarten   
4         PT9354                    DISCOVERY KIDZ EMPIRE PTE. LTD.   
...          ...                                                ...   
1890          na  PCF Sparkletots Preschool @ Queenstown Blk 78B...   
1891          na                             MY World Preschool Ltd   
1892          na                     Skool4kidz@Sembawang EastCreek   
1893          na          PCF SPARLETOTS PRESCHOOL @ JOO CHIAT (DS)   
1894          na                  Skool4Kidz Campus @ Fernvale Lane   

                                    centre_address postal_code infant_vacancy  \
0               679 CHOA CHU KANG CRESCENT #01-602      680679             na   
1                               09 WINCHESTER ROAD      117783             na   
2         1 STADIUM PLACE #01-24 KALLANG WAVE MALL      397628             na   
3                 blk 255 Bishan Street 22 #04-454      570255             na   
4                 96 FARRER ROAD CHIP HOCK GARDENS      259225             na   
...                                            ...         ...            ...   
1890                  78B Strathmore Avenue #02-01      143078             na   
1891  132 Canberra View #03-01 Eastlink @ Canberra      750132             na   
1892                           101 Canberra Street      750101             na   
1893                       15 LORONG K TELOK KURAU      425611             na   
1894                       60 Sengkang West Avenue          na             na   

     pg_vacancy n1_vacancy n2_vacancy k1_vacancy k2_vacancy  \
0     Immediate  Immediate  Immediate  Immediate  Immediate   
1            na         na         na         na         na   
2            na         na         na         na         na   
3            na         na         na         na         na   
4            na         na         na         na         na   
...         ...        ...        ...        ...        ...   
1890         na         na         na         na         na   
1891         na         na         na         na         na   
1892         na         na         na         na         na   
1893         na         na         na         na         na   
1894         na         na         na         na         na   

                                           food_offered spark_certified  \
0     No Pork No Lard with No Beef (without Certific...              No   
1     No Pork No Lard with No Beef (without Certific...              No   
2     No Pork No Lard with No Beef (from Non-Halal S...              No   
3                                                    na              No   
4     No Pork No Lard with No Beef (without Certific...              No   
...                                                 ...             ...   
1890  No Pork No Lard with No Beef (without Certific...              No   
1891  No Pork No Lard with No Beef (without Certific...              No   
1892  No Pork No Lard with No Beef (from Non-Halal S...              No   
1893  No Pork No Lard with No Beef (without Certific...              No   
1894  No Pork No Lard with No Beef (without Certific...              No   

     weekday_full_day provision_of_transport government_subsidy       lat  \
0         07:00-19:00                     No                Yes  1.402393   
1         07:00-19:00                    Yes                Yes  1.286135   
2         07:00-19:00                     No                Yes  1.303224   
3         08:00-13:00                    Yes                Yes  1.361652   
4         07:00-19:00                    Yes                Yes  1.319813   
...               ...                    ...               

## Clean location data

In [62]:
# Check how many addresses do not have coordinate data
no_data = df2['lat'].isna().sum()

print("There are {} centers with no coordinate data".format(no_data))
print('--- Dropping locations with no data ---')


# Decide to drop locations with no data
df2 = df2.dropna(axis =0)
no_data = df2['lat'].isna().sum()
print("There are now {} centers with no coordinate data".format(no_data))


There are 82 centers with no coordinate data
--- Dropping locations with no data ---
There are now 0 centers with no coordinate data


## Add MRT location data

Data available in Singapore Land Transport Authority website / Kaggle

In [13]:
df_mrt = pd.read_csv('mrt_lrt_data.csv')
df_mrt

station_name type       lat         lng
0      Jurong East  MRT  1.333207  103.742308
1      Bukit Batok  MRT  1.349069  103.749596
2     Bukit Gombak  MRT  1.359043  103.751863
3    Choa Chu Kang  MRT  1.385417  103.744316
4          Yew Tee  MRT  1.397383  103.747523
..             ...  ...       ...         ...
152  Punggol Point  LRT  1.416932  103.906680
153       Samudera  LRT  1.415955  103.902185
154         Nibong  LRT  1.411865  103.900321
155         Sumang  LRT  1.408501  103.898605
156       Soo Teck  LRT  1.405436  103.897287

[157 rows x 4 columns]

## Generate Singapore Map

In [243]:
address = 'Singapore'

geolocator = Nominatim(user_agent="SG_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Singapore are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Singapore are 1.357107, 103.8194992.


## Add Childcare and MRT location to the map

In [244]:
map_SG = folium.Map(location=[latitude, longitude], zoom_start=10)

# add center markers to map
for lat, lng, name, address in zip(df2['lat'], df2['lng'], df2['centre_name'], df2['centre_address']):
    label = '{}, {}'.format(name, address)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_SG)
    
# add MRT markers to map
for lat, lng, name in zip(df_mrt['lat'], df_mrt['lng'], df_mrt['station_name']):
    label = '{}'.format(name)
    label = folium.Popup(label, parse_html=True)
    folium.Marker(
        [lat, lng],
        popup=label,
        icon=folium.Icon(color='lightgray', icon_color='white',icon='subway', prefix='fa')
    ).add_to(map_SG)  
    

# draw radius from MRT station
for lat, lng in zip(df_mrt['lat'], df_mrt['lng']):
    folium.Circle(
        [lat, lng],
        radius=500,
        color='crimson',
        fill=False,
    ).add_to(map_SG)
    
map_SG

## Calculate distance of every childcare centers to all MRT

In [15]:
# Zip the latitude and longitude data together to calculate distance

mrt_coord = zip(df_mrt['lat'], df_mrt['lng']) 
centre_coord = zip(df2['lat'], df2['lng'])
mrt_coord = tuple(mrt_coord)
centre_coord = tuple(centre_coord)
mrt_coord[0]

(1.333207, 103.742308)

In [16]:
# Test distance calculation using geopy distance formula

geopy.distance.distance(mrt_coord[1],centre_coord[1]).m

8579.099277653826

In [198]:
# generate empty dataframe to house the distance data

df_dist = pd.DataFrame(columns = df_mrt['station_name'].values)
df_dist

Empty DataFrame
Columns: [Jurong East, Bukit Batok, Bukit Gombak, Choa Chu Kang, Yew Tee, Kranji, Marsiling, Woodlands, Admiralty, Sembawang, Yishun, Khatib, Yio Chu Kang, Ang Mo Kio, Bishan, Braddell, Toa Payoh, Novena, Newton, Orchard, Somerset, Dhoby Ghaut, City Hall, Raffles Place, Marina Bay, Marina South Pier, Tuas Link, Tuas West Road, Tuas Crescent, Gul Circle, Joo Koon, Pioneer, Boon Lay, Lakeside, Chinese Garden, Clementi, Dover, Buona Vista, Commonwealth, Queenstown, Redhill, Tiong Bahru, Outram Park, Tanjong Pagar, Bugis, Lavender, Kallang, Aljunied, Paya Lebar, Eunos, Kembangan, Bedok, Tanah Merah, Simei, Tampines, Pasir Ris, Expo, Changi Airport, HarbourFront, Chinatown, Clarke Quay, Little India, Farrer Park, Boon Keng, Potong Pasir, Woodleigh, Serangoon, Kovan, Hougang, Buangkok, Sengkang, Punggol, Bras Basah, Esplanade, Promenade, Nicoll Highway, Stadium, Mountbatten, Dakota, MacPherson, Tai Seng, Bartley, Lorong Chuan, Marymount, Caldecott, Botanic Gardens, Farrer Road, Holland Village, one-north, Kent Ridge, Haw Par Villa, Pasir Panjang, Labrador Park, Telok Blangah, Bayfront, Bukit Panjang, Cashew, Hillview, Beauty World, King Albert Park, ...]
Index: []

[0 rows x 157 columns]

In [197]:
#df_dist.index
df_dist.columns[0]

'centre_name'

In [19]:
# Calculate distance for all childcare services to all MRT

dist_dict = {}

for x in range(len(mrt_coord)):
    for y in range(len(centre_coord)):
        dist = geopy.distance.distance(mrt_coord[x],centre_coord[y]).m
        dict_key = x
        dist_dict.setdefault(dict_key,[])
        dist_dict[dict_key].append(dist)
        

In [199]:
# Input distance data to dataframe

for z in range(len(df_dist.columns)):
    df_dist.iloc[:,z] = dist_dict[z]


In [217]:
df_dist.insert(0, column='centre_name',value=df2['centre_name'])
df_dist = df_dist.set_index('centre_name')
df_dist

Jurong East   Bukit Batok  \
centre_name                                                              
KINDERYEARS CHILDCARE & DEVELOPMENT CENTRE   7653.354114   5926.001912   
LORNA WHISTON PRE-SCHOOL                     7814.304700   8579.099278   
LORNA WHISTON PRE-SCHOOL                    14903.853035  14625.894840   
Jessin Kindergarten                         11611.845809  10459.594675   
DISCOVERY KIDZ EMPIRE PTE. LTD.              7853.088136   7621.667419   
...                                                  ...           ...   
MY FIRST SKOOL                               3532.186707   4494.759635   
OUR FIRST STEPS PRESCHOOL PTE. LTD.          7381.019007   8176.664944   
MINDCHAMPS PRESCHOOL @ YISHUN PTE. LTD.     22892.732804  22026.780007   
THE GLITTER RAINBOW SKOOL PTE. LTD.          6216.604080   4322.714054   
MY FIRST SKOOL                              18546.933097  18055.282235   

                                            Bukit Gombak  Choa Chu Kang  \
centre_name                                                               
KINDERYEARS CHILDCARE & DEVELOPMENT CENTRE   4867.314224    1877.126741   
LORNA WHISTON PRE-SCHOOL                     9364.759631   12326.166606   
LORNA WHISTON PRE-SCHOOL                    14814.013228   16949.473435   
Jessin Kindergarten                         10118.441698   11264.947959   
DISCOVERY KIDZ EMPIRE PTE. LTD.              7938.703095   10426.038706   
...                                                  ...            ...   
MY FIRST SKOOL                               5443.158844    8477.856245   
OUR FIRST STEPS PRESCHOOL PTE. LTD.          8980.988217   11956.293207   
MINDCHAMPS PRESCHOOL @ YISHUN PTE. LTD.     21810.567001   22996.951421   
THE GLITTER RAINBOW SKOOL PTE. LTD.          3339.538418    3345.594795   
MY FIRST SKOOL                              18093.436991   19896.560761   

                                                 Yew Tee        Kranji  \
centre_name                                                              
KINDERYEARS CHILDCARE & DEVELOPMENT CENTRE    661.716396   3214.207535   
LORNA WHISTON PRE-SCHOOL                    13373.950035  15811.059717   
LORNA WHISTON PRE-SCHOOL                    17406.895996  18284.527941   
Jessin Kindergarten                         11309.793055  11409.922248   
DISCOVERY KIDZ EMPIRE PTE. LTD.             11154.875367  12902.539796   
...                                                  ...           ...   
MY FIRST SKOOL                               9671.759709  12546.304356   
OUR FIRST STEPS PRESCHOOL PTE. LTD.         13021.741121  15509.911333   
MINDCHAMPS PRESCHOOL @ YISHUN PTE. LTD.     22927.251741  22356.775261   
THE GLITTER RAINBOW SKOOL PTE. LTD.          3524.432987   5217.814855   
MY FIRST SKOOL                              20153.885871  20464.920309   

                                               Marsiling     Woodlands  \
centre_name                                                              
KINDERYEARS CHILDCARE & DEVELOPMENT CENTRE   4711.404208   6051.175356   
LORNA WHISTON PRE-SCHOOL                    16353.419489  16705.509877   
LORNA WHISTON PRE-SCHOOL                    18035.798926  17645.151049   
Jessin Kindergarten                         10944.658801  10425.876561   
DISCOVERY KIDZ EMPIRE PTE. LTD.             13147.393731  13256.230016   
...                                                  ...           ...   
MY FIRST SKOOL                              13374.499303  14016.412527   
OUR FIRST STEPS PRESCHOOL PTE. LTD.         16083.391086  16466.423578   
MINDCHAMPS PRESCHOOL @ YISHUN PTE. LTD.     21459.748919  20472.956365   
THE GLITTER RAINBOW SKOOL PTE. LTD.          5855.388188   6495.106577   
MY FIRST SKOOL                              19943.496962  19294.298356   

                                               Admiralty     Sembawang  ...  \
centre_name                                                             ...   
KINDERYEARS CHILDCARE 

## Count how many centers are within 500m radius to each MRT station

In [226]:
num_nearby_center = df_dist[df_dist < 500].count()
num_nearby_center = num_nearby_center.sort_values(ascending=False)
print(num_nearby_center)
print('==============================================================')
print('Avg number of centers per location: ' + str(int(num_nearby_center.mean())))
print('Top quartile number of centers per location: ' + str(num_nearby_center.quantile(0.75)))

Compassvale          21
South View           17
Keat Hong            17
Meridian             16
Cove                 15
                     ..
Gul Circle            0
Kranji                0
Joo Koon              0
Marina South Pier     0
Tuas Link             0
Length: 157, dtype: int64
Avg number of centers per location: 6
Top quartile number of centers per location: 9.0


In [32]:
# Merge number of centers data to MRT location dataframe
df_mrt['number of centers nearby'] = num_nearby_center
df_mrt

station_name type       lat         lng  number of centers nearby
0      Jurong East  MRT  1.333207  103.742308                         6
1      Bukit Batok  MRT  1.349069  103.749596                        11
2     Bukit Gombak  MRT  1.359043  103.751863                         6
3    Choa Chu Kang  MRT  1.385417  103.744316                         6
4          Yew Tee  MRT  1.397383  103.747523                        11
..             ...  ...       ...         ...                       ...
152  Punggol Point  LRT  1.416932  103.906680                         3
153       Samudera  LRT  1.415955  103.902185                         4
154         Nibong  LRT  1.411865  103.900321                         7
155         Sumang  LRT  1.408501  103.898605                         9
156       Soo Teck  LRT  1.405436  103.897287                         8

[157 rows x 5 columns]

## Let's filter good MRT stations for those with more than 9 nearby childcare centers (top quartile)
... and also let's filter out LRT locations

In [255]:
df_mrt_good = df_mrt.loc[(df_mrt['number of centers nearby'] >= 9) & (df_mrt['type'] == 'MRT')]
df_mrt_good = df_mrt_good.sort_values(by='number of centers nearby', ascending=False)
df_mrt_good

station_name type       lat         lng  number of centers nearby
31         Pioneer  MRT  1.337645  103.697420                        14
54        Tampines  MRT  1.354467  103.943325                        14
105     Telok Ayer  MRT  1.282285  103.848584                        12
77     Mountbatten  MRT  1.306106  103.883175                        12
1      Bukit Batok  MRT  1.349069  103.749596                        11
9        Sembawang  MRT  1.449133  103.820060                        11
18          Newton  MRT  1.313830  103.838021                        11
4          Yew Tee  MRT  1.397383  103.747523                        11
66       Serangoon  MRT  1.349862  103.873635                        10
98    Beauty World  MRT  1.341607  103.775682                        10
95   Bukit Panjang  MRT  1.378340  103.762452                        10
43   Tanjong Pagar  MRT  1.276385  103.846771                        10
71         Punggol  MRT  1.405191  103.902367                        10
109      Bendemeer  MRT  1.313674  103.863098                         9
47        Aljunied  MRT  1.316474  103.882762                         9
64    Potong Pasir  MRT  1.331316  103.868779                         9
53           Simei  MRT  1.343237  103.953343                         9
35        Clementi  MRT  1.314925  103.765341                         9
32        Boon Lay  MRT  1.338620  103.705817                         9
11          Khatib  MRT  1.417423  103.832995                         9
10          Yishun  MRT  1.429666  103.835044                         9
6        Marsiling  MRT  1.432579  103.774150                         9
117  Tampines East  MRT  1.356310  103.955471                         9

In [245]:
# Mark good MRT locations in map

for lat, lng, name in zip(df_mrt_good['lat'], df_mrt_good['lng'], df_mrt_good['station_name']):
        label = '{}'.format(name)
        label = folium.Popup(label, parse_html=True)
        folium.Marker(
            [lat, lng],
            popup=label,
            icon=folium.Icon(color='green', icon_color='white',icon='subway', prefix='fa')
        ).add_to(map_SG)  
        
map_SG

## Now that we have filtered good MRT locations, let's find nearby amenities in these stations

In [256]:
# load API key

with open('API_Key.json') as json_data:
    API_Key = json.load(json_data)

FS_ID = API_Key['Foursquare_CLIENT_ID']
FS_SECRET = API_Key['Foursquare_CLIENT_SECRET']
VERSION = '20200404' # Foursquare API version

### First, let's do some test run

In [251]:
mrt_lat = df_mrt_good['lat'].values
mrt_lng = df_mrt_good['lng'].values
mrt_name = df_mrt_good['station_name'].values

print('Latitude and longitude values of {} are {}, {}.'.format(mrt_name, 
                                                               mrt_lat, 
                                                               mrt_lng))

Latitude and longitude values of ['Pioneer' 'Tampines' 'Telok Ayer' 'Mountbatten' 'Bukit Batok' 'Sembawang'
 'Newton' 'Yew Tee' 'Serangoon' 'Beauty World' 'Bukit Panjang'
 'Tanjong Pagar' 'Punggol' 'Bendemeer' 'Aljunied' 'Potong Pasir' 'Simei'
 'Clementi' 'Boon Lay' 'Khatib' 'Yishun' 'Marsiling' 'Tampines East'] are [1.337645 1.354467 1.282285 1.306106 1.349069 1.449133 1.31383  1.397383
 1.349862 1.341607 1.37834  1.276385 1.405191 1.313674 1.316474 1.331316
 1.343237 1.314925 1.33862  1.417423 1.429666 1.432579 1.35631 ], [103.69742  103.943325 103.848584 103.883175 103.749596 103.82006
 103.838021 103.747523 103.873635 103.775682 103.762452 103.846771
 103.902367 103.863098 103.882762 103.868779 103.953343 103.765341
 103.705817 103.832995 103.835044 103.77415  103.955471].


In [264]:
limit = 100
radius = 500

url2 = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    FS_ID, 
    FS_SECRET, 
    VERSION, 
    mrt_lat[0], 
    mrt_lng[0], 
    radius, 
    limit)
url2


'https://api.foursquare.com/v2/venues/explore?&client_id=NZB4TP0TKL35XVBADLFORZLSPC1YMIU5IW0OYFN0F0GI3NHJ&client_secret=2BG1LOJ4ZM12JUVZWCZTVLIZMYSUFZWFZMO1PSX4UAXNFDXU&v=20200404&ll=1.337645,103.69742&radius=500&limit=100'

In [265]:
results = requests.get(url2).json()
results

{'meta': {'code': 200, 'requestId': '5e894dcdd03993001bce5674'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Jurong West',
  'headerFullLocation': 'Jurong West, Singapore',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 13,
  'suggestedBounds': {'ne': {'lat': 1.3421450045000045,
    'lng': 103.70191282682907},
   'sw': {'lat': 1.3331449954999954, 'lng': 103.69292717317092}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4c90b239238c6dcb9951b955',
       'name': 'Jurong West Swimming Complex',
       'location': {'address': 'Jurong West Sports And Recreation Centre/Stadium',
        'crossStreet': '20 Jurong West St 93',
        'lat': 1.338226962073866,
    

In [266]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [268]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues

name            categories       lat  \
0               Jurong West Swimming Complex                  Pool  1.338227   
1                   Jurong West ActiveSg Gym  Gym / Fitness Center  1.337921   
2                                 McDonald's  Fast Food Restaurant  1.341658   
3   Jurong West Sports and Recreation Centre               Stadium  1.338494   
4               Bus Stop 22451 (opp Blk 643)           Bus Station  1.338356   
5        Driving Range @ Jurong Country Club           Golf Course  1.336386   
6               Playground@jurong West St 61            Playground  1.336403   
7                       SBS Transit: Bus 255              Bus Line  1.339491   
8                                Giant Hyper           Supermarket  1.342019   
9                   Bus Stop 22231 (Blk 639)              Bus Stop  1.340771   
10                          Swee Heng Bakery                Bakery  1.340465   
11                              Pioneer Mall         Shopping Mall  1.341845   
12                    Yang Ming Yuan Nursery           Flower Shop  1.336119   

           lng  
0   103.694012  
1   103.694515  
2   103.696834  
3   103.694876  
4   103.695806  
5   103.698497  
6   103.698483  
7   103.697201  
8   103.697088  
9   103.697253  
10  103.695386  
11  103.696986  
12  103.693798

... test run looking good ...
## Now let's find nearby amenities foor all good MRT locations

In [276]:
limit = 100


def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url2 = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            FS_ID, 
            FS_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            limit)
            
        # make the GET request
        results = requests.get(url2).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['MRT', 
                  'MRT Latitude', 
                  'MRT Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [277]:
nearby_amenities = getNearbyVenues(names=df_mrt_good['station_name'],
                                   latitudes=df_mrt_good['lat'],
                                   longitudes=df_mrt_good['lng'],
                                   )

Pioneer
Tampines
Telok Ayer
Mountbatten
Bukit Batok
Sembawang
Newton
Yew Tee
Serangoon
Beauty World
Bukit Panjang
Tanjong Pagar
Punggol
Bendemeer
Aljunied
Potong Pasir
Simei
Clementi
Boon Lay
Khatib
Yishun
Marsiling
Tampines East


In [279]:
nearby_amenities.groupby('MRT').count()

MRT Latitude  MRT Longitude  Venue  Venue Latitude  \
MRT                                                                 
Aljunied                 55             55     55              55   
Beauty World             79             79     79              79   
Bendemeer                20             20     20              20   
Boon Lay                 67             67     67              67   
Bukit Batok              23             23     23              23   
Bukit Panjang            50             50     50              50   
Clementi                 65             65     65              65   
Khatib                   21             21     21              21   
Marsiling                15             15     15              15   
Mountbatten              58             58     58              58   
Newton                   28             28     28              28   
Pioneer                  13             13     13              13   
Potong Pasir             36             36     36              36   
Punggol                  46             46     46              46   
Sembawang                15             15     15              15   
Serangoon                40             40     40              40   
Simei                    22             22     22              22   
Tampines                 90             90     90              90   
Tampines East             9              9      9               9   
Tanjong Pagar           100            100    100             100   
Telok Ayer              100            100    100             100   
Yew Tee                  12             12     12              12   
Yishun                   50             50     50              50   

               Venue Longitude  Venue Category  
MRT                                             
Aljunied                    55              55  
Beauty World                79              79  
Bendemeer                   20              20  
Boon Lay                    67              67  
Bukit Batok                 23              23  
Bukit Panjang               50              50  
Clementi                    65              65  
Khatib                      21              21  
Marsiling                   15              15  
Mountbatten                 58              58  
Newton                      28              28  
Pioneer                     13              13  
Potong Pasir                36              36  
Punggol                     46              46  
Sembawang                   15              15  
Serangoon                   40              40  
Simei                       22              22  
Tampines                    90              90  
Tampines East                9               9  
Tanjong Pagar              100             100  
Telok Ayer                 100             100  
Yew Tee                     12              12  
Yishun                      50              50

In [295]:
print(nearby_amenities['Venue Category'].unique())
print('=====================================================================')
print('There are {} uniques categories.'.format(len(nearby_amenities['Venue Category'].unique())))

['Pool' 'Gym / Fitness Center' 'Fast Food Restaurant' 'Stadium'
 'Bus Station' 'Golf Course' 'Playground' 'Bus Line' 'Supermarket'
 'Bus Stop' 'Bakery' 'Shopping Mall' 'Flower Shop' 'Thai Restaurant' 'Gym'
 'Fried Chicken Joint' 'Coffee Shop' 'Dessert Shop' 'Clothing Store'
 'Chinese Restaurant' 'Spa' 'Skate Park' 'Japanese Restaurant'
 'Dumpling Restaurant' 'Café' 'Steakhouse' 'Toy / Game Store' 'Bookstore'
 'Hotpot Restaurant' 'Asian Restaurant' 'Indonesian Restaurant'
 'Bubble Tea Shop' 'American Restaurant' 'Indian Restaurant'
 'Mediterranean Restaurant' 'Seafood Restaurant' 'Portuguese Restaurant'
 'Food Court' 'Sushi Restaurant' 'Pharmacy' 'Soup Place' 'Snack Place'
 'Donut Shop' 'Korean Restaurant' 'Ice Cream Shop' 'Sandwich Place'
 'Department Store' 'Park' 'Restaurant' 'Lingerie Store'
 'Dim Sum Restaurant' 'Bowling Alley' 'Athletics & Sports' 'Soccer Field'
 'Wine Bar' 'Hotel' 'Vietnamese Restaurant' 'Beer Garden'
 'Martial Arts Dojo' 'Bar' 'Modern European Restaurant'
 'Fren

### ... There are too many categories, let's narrow it down ...

In [365]:
Resto = ['Restaurant','Steakhouse','Soup Place','Noodle House','Burrito Place','Pizza Place','BBQ Joint','Bistro','Diner','Chinese Breakfast Place','Breakfast Spot','Cha Chaan Teng','Wings Joint','Burger Joint','Fried Chicken Joint','Salad Place','Food']
Cafe = ['Bakery','Coffee Shop','Dessert Shop','Café','Bubble Tea Shop','Snack Place','Donut Shop','Ice Cream Shop','Sandwich Place','Deli / Bodega','Cupcake Shop','Frozen Yogurt Shop','Juice Bar','Bagel Shop','Tea Room','Food_Court']
Food_Court = ['Food Court','Street Food Gathering','Food Truck']
Gym = ['Gym','Athletics & Sports','Martial Arts Dojo','Yoga Studio','Climbing Gym','Tennis Court','Badminton Court','Dance Studio']
Bar = ['Beer Garden','Bar','Speakeasy','Cocktail Bar','Lounge','Brewery','Hotel Bar','Beer Bar','Nightclub','Other Nightlife']
Grocery = ['Supermarket','Farmers Market','Market','Food & Drink Shop','Grocery Store']
Shopping = ['Shopping Mall','Flower Shop','Clothing Store','Toy / Game Store','Bookstore','Department Store','Lingerie Store','Sporting Goods Shop',
            'Video Store','Cosmetics Shop','Plaza','Kids Store','Pet Store','Thrift / Vintage Store','Electronics Store','Beer Store','Liquor Store',
            'Pedestrian Plaza','Discount Store','Shoe Store','Optical Shop','Kitchen Supply Store','Video Game Store','Arts & Crafts Store',"Women's Store",
            'Smoke Shop','Furniture','Jewelry Store','Pharmacy','Convenience Store']
Park = ['Pool','Park','Other Great Outdoors','Trail','Dog Run','Golf Course','Playground','Soccer Field','Scenic Lookout','Sports Club','Garden','Recreation Center','Stadium']
Art = ['Art','Multiplex','Bowling Alley','Entertainment','Arcade','Photography']
Transport = ['Bus','Taxi','Train','Tunnel','Station']
Residential = ['Hostel','Boarding House','Residential']
Bank = ['Bank','ATM']
Spa = ['Spa','Massage']
Lottery = ['Lottery','Betting']
Religion = ['Temple','Mosque']
Doctor = ['Doctor','Dentist','Vet']

nearby_amenities.loc[nearby_amenities['Venue Category'].str.contains('|'.join(Resto)), 'Venue Category'] = 'Restaurant'
nearby_amenities.loc[nearby_amenities['Venue Category'].str.contains('|'.join(Cafe)), 'Venue Category'] = 'Cafe / Dessert'
nearby_amenities.loc[nearby_amenities['Venue Category'].str.contains('|'.join(Food_Court)), 'Venue Category'] = 'Food Court'
nearby_amenities.loc[nearby_amenities['Venue Category'].str.contains('|'.join(Gym)), 'Venue Category'] = 'Gym / Fitness Center'
nearby_amenities.loc[nearby_amenities['Venue Category'].str.contains('|'.join(Bar)), 'Venue Category'] = 'Bar / Nightlife'
nearby_amenities.loc[nearby_amenities['Venue Category'].str.contains('|'.join(Grocery)), 'Venue Category'] = 'Grocery / Market'
nearby_amenities.loc[nearby_amenities['Venue Category'].str.contains('|'.join(Shopping)), 'Venue Category'] = 'Malls / Shops'
nearby_amenities.loc[nearby_amenities['Venue Category'].str.contains('|'.join(Park)), 'Venue Category'] = 'Park / Outdoor Activities'
nearby_amenities.loc[nearby_amenities['Venue Category'].str.contains('|'.join(Art)), 'Venue Category'] = 'Art / Entertainment'
nearby_amenities.loc[nearby_amenities['Venue Category'].str.contains('|'.join(Transport)), 'Venue Category'] = 'Transportation'
nearby_amenities.loc[nearby_amenities['Venue Category'].str.contains('|'.join(Residential)), 'Venue Category'] = 'Residential'
nearby_amenities.loc[nearby_amenities['Venue Category'].str.contains('|'.join(Bank)), 'Venue Category'] = 'Bank / ATM'
nearby_amenities.loc[nearby_amenities['Venue Category'].str.contains('|'.join(Spa)), 'Venue Category'] = 'Spa / Massage'
nearby_amenities.loc[nearby_amenities['Venue Category'].str.contains('|'.join(Lottery)), 'Venue Category'] = 'Lottery'
nearby_amenities.loc[nearby_amenities['Venue Category'].str.contains('|'.join(Religion)), 'Venue Category'] = 'Church / Temple / Mosque'
nearby_amenities.loc[nearby_amenities['Venue Category'].str.contains('|'.join(Doctor)), 'Venue Category'] = 'Doctor / Dentist / Vet'

In [366]:
print(nearby_amenities['Venue Category'].unique())
print('=====================================================================')
print('There are {} uniques categories.'.format(len(nearby_amenities['Venue Category'].unique())))

['Park / Outdoor Activities' 'Gym / Fitness Center' 'Restaurant'
 'Transportation' 'Grocery / Market' 'Cafe / Dessert' 'Malls / Shops'
 'Spa / Massage' 'Art / Entertainment' 'Bar / Nightlife' 'Hotel'
 'Church / Temple / Mosque' 'Residential' 'Bank / ATM' 'Lottery'
 'Doctor / Dentist / Vet']
There are 16 uniques categories.


## Looking good now. Let's filter locations with amenities important to us to get best locations

In [383]:
imp_amenities = ['Restaurant','Grocery / Market','Park / Outdoor Activities','Gym / Fitness Center']
df_mrt_best = nearby_amenities[nearby_amenities['Venue Category'].isin(imp_amenities)]
df_mrt_best

MRT  MRT Latitude  MRT Longitude  \
0           Pioneer      1.337645     103.697420   
1           Pioneer      1.337645     103.697420   
2           Pioneer      1.337645     103.697420   
3           Pioneer      1.337645     103.697420   
5           Pioneer      1.337645     103.697420   
...             ...           ...            ...   
1000      Marsiling      1.432579     103.774150   
1003      Marsiling      1.432579     103.774150   
1004      Marsiling      1.432579     103.774150   
1006  Tampines East      1.356310     103.955471   
1010  Tampines East      1.356310     103.955471   

                                         Venue  Venue Latitude  \
0                 Jurong West Swimming Complex        1.338227   
1                     Jurong West ActiveSg Gym        1.337921   
2                                   McDonald's        1.341658   
3     Jurong West Sports and Recreation Centre        1.338494   
5          Driving Range @ Jurong Country Club        1.336386   
...                                        ...             ...   
1000                        Noelle's Signature        1.429906   
1003                  香港街@woodlands Block 306A        1.429550   
1004           Playground Between Blk 168 &173        1.433162   
1006                            Domino's Pizza        1.357335   
1010                                McDonald's        1.353141   

      Venue Longitude             Venue Category  
0          103.694012  Park / Outdoor Activities  
1          103.694515       Gym / Fitness Center  
2          103.696834                 Restaurant  
3          103.694876  Park / Outdoor Activities  
5          103.698497  Park / Outdoor Activities  
...               ...                        ...  
1000       103.773608                 Restaurant  
1003       103.775297                 Restaurant  
1004       103.777456  Park / Outdoor Activities  
1006       103.953207                 Restaurant  
1010       103.954494                 Restaurant  

[559 rows x 7 columns]

## Now lets do one hot encoding

In [386]:
# one hot encoding
mrt_best_onehot = pd.get_dummies(df_mrt_best[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
mrt_best_onehot['MRT'] = df_mrt_best['MRT'] 

# move neighborhood column to the first column
fixed_columns = [mrt_best_onehot.columns[-1]] + list(mrt_best_onehot.columns[:-1])
mrt_best_onehot = mrt_best_onehot[fixed_columns]

print(mrt_best_onehot.shape)
mrt_best_onehot.head()


(559, 5)


MRT  Grocery / Market  Gym / Fitness Center  Park / Outdoor Activities  \
0  Pioneer                 0                     0                          1   
1  Pioneer                 0                     1                          0   
2  Pioneer                 0                     0                          0   
3  Pioneer                 0                     0                          1   
5  Pioneer                 0                     0                          1   

   Restaurant  
0           0  
1           0  
2           1  
3           0  
5           0

In [428]:
mrt_best_grouped = mrt_best_onehot.groupby('MRT').sum().reset_index()
#mrt_best_grouped.insert(1,column='Childcare',value = df_mrt_good['number of centers nearby'].values)
dfx = df_mrt_good.set_index('station_name')
mrt_best_grouped = mrt_best_grouped.set_index('MRT')
mrt_best_grouped['Childcare'] = dfx['number of centers nearby']
mrt_best_grouped = mrt_best_grouped.reset_index()
mrt_best_grouped

MRT  Grocery / Market  Gym / Fitness Center  \
0        Aljunied                 1                     2   
1    Beauty World                 2                     0   
2       Bendemeer                 1                     0   
3        Boon Lay                 1                     1   
4     Bukit Batok                 1                     0   
5   Bukit Panjang                 1                     2   
6        Clementi                 3                     2   
7          Khatib                 4                     0   
8       Marsiling                 2                     0   
9     Mountbatten                 2                     6   
10         Newton                 1                     2   
11        Pioneer                 1                     1   
12   Potong Pasir                 1                     0   
13        Punggol                 2                     1   
14      Sembawang                 1                     0   
15      Serangoon                 1                     0   
16          Simei                 0                     1   
17       Tampines                 2                     5   
18  Tampines East                 0                     0   
19  Tanjong Pagar                 0                     4   
20     Telok Ayer                 0                     7   
21        Yew Tee                 0                     0   
22         Yishun                 3                     0   

    Park / Outdoor Activities  Restaurant  Childcare  
0                           0          33          9  
1                           0          40         10  
2                           0          11          9  
3                           4          36          9  
4                           3           6         11  
5                           0          26         10  
6                           0          29          9  
7                           1           5          9  
8                           1           6          9  
9                           1          31         12  
10                          0          18         11  
11                          4           1         14  
12                          1          11          9  
13                          2          20         10  
14                          0           6         11  
15                          2          16         10  
16                          0          11          9  
17                          5          37         14  
18                          0           2          9  
19                          2          48         10  
20                          2          44         12  
21                          1           4         11  
22                          1          24          9

## Let's try to cluster the MRT / neighborhoods and see what it returns

In [429]:
# set number of clusters
kclusters = 3

MRT_grouped_clustering = mrt_best_grouped.drop('MRT', 1)
# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(amenities_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 1, 0, 1, 0, 0, 1, 1, 0], dtype=int32)

In [430]:
# add clustering labels
mrt_best_grouped.insert(1, 'Cluster Labels', kmeans.labels_)

In [433]:
# Add back coordinate data for each location
mrt_best_merged = mrt_best_grouped.set_index('MRT')
mrt_best_merged['lat'] = dfx['lat']
mrt_best_merged['lng'] = dfx['lng']
mrt_best_merged = mrt_best_merged.reset_index()
mrt_best_merged

MRT  Cluster Labels  Grocery / Market  Gym / Fitness Center  \
0        Aljunied               0                 1                     2   
1    Beauty World               0                 2                     0   
2       Bendemeer               1                 1                     0   
3        Boon Lay               0                 1                     1   
4     Bukit Batok               1                 1                     0   
5   Bukit Panjang               0                 1                     2   
6        Clementi               0                 3                     2   
7          Khatib               1                 4                     0   
8       Marsiling               1                 2                     0   
9     Mountbatten               0                 2                     6   
10         Newton               1                 1                     2   
11        Pioneer               1                 1                     1   
12   Potong Pasir               1                 1                     0   
13        Punggol               0                 2                     1   
14      Sembawang               1                 1                     0   
15      Serangoon               1                 1                     0   
16          Simei               1                 0                     1   
17       Tampines               0                 2                     5   
18  Tampines East               1                 0                     0   
19  Tanjong Pagar               2                 0                     4   
20     Telok Ayer               2                 0                     7   
21        Yew Tee               1                 0                     0   
22         Yishun               0                 3                     0   

    Park / Outdoor Activities  Restaurant  Childcare       lat         lng  
0                           0          33          9  1.316474  103.882762  
1                           0          40         10  1.341607  103.775682  
2                           0          11          9  1.313674  103.863098  
3                           4          36          9  1.338620  103.705817  
4                           3           6         11  1.349069  103.749596  
5                           0          26         10  1.378340  103.762452  
6                           0          29          9  1.314925  103.765341  
7                           1           5          9  1.417423  103.832995  
8                           1           6          9  1.432579  103.774150  
9                           1          31         12  1.306106  103.883175  
10                          0          18         11  1.313830  103.838021  
11                          4           1         14  1.337645  103.697420  
12                          1          11          9  1.331316  103.868779  
13                          2          20         10  1.405191  103.902367  
14                          0           6         11  1.449133  103.820060  
15                          2          16         10  1.349862  103.873635  
16                          0          11          9  1.343237  103.953343  
17                          5          37         14  1.354467  103.943325  
18                          0           2          9  1.356310  103.955471  
19                          2          48         10  1.276385  103.846771  
20                          2          44         12  1.282285  103.848584  
21                          1           4         11  1.397383  103.747523  
22                          1          24          9  1.429666  103.835044

### Looks good, now lets mark it on the map

In [440]:
# Mark best MRT locations in map with cluster label

for lat, lng, name, cluster, childcare, grocery, gym, park, restaurant in zip(mrt_best_merged['lat'], mrt_best_merged['lng'], mrt_best_merged['MRT'], mrt_best_merged['Cluster Labels'],
                                                                              mrt_best_merged['Childcare'], mrt_best_merged['Grocery / Market'], mrt_best_merged['Gym / Fitness Center'], 
                                                                              mrt_best_merged['Park / Outdoor Activities'], mrt_best_merged['Restaurant']):
        label = '{}, Cluster: {}, Childcare: {}, Grocery/Market: {}, Gym/Fitness Center: {}, Park/Outdoor Activities: {}, Restaurant: {}'.format(name,cluster, childcare, grocery, gym, park, restaurant)
        label = folium.Popup(label, parse_html=True)
        folium.Marker(
            [lat, lng],
            popup=label,
            icon=folium.Icon(color='darkred', icon_color='white',icon='subway', prefix='fa')
        ).add_to(map_SG)  
        
map_SG

# Conclusion

In considering neighborhoods to live in Singapore, families with working parents and young children that need childcare service may want to consider two primary factors:
- Number of available childcare centers nearby to maximize their chance to get a slot (childcare services are highly in demand)
- Proximity to a MRT station for convenience (especially if they rely on public transport to commute)

There are 23 MRT stations / neighborhoods with at least 9 childcare services (top quartile) within the radius of 500 meters. 

We narrowed down the list further by adding another dimension: availability of important amenities nearby.

Our clustering exercise appear to suggest that locations labeled with cluster '0' meet most of our criteria and there are 9 locations in this category.

By analyzing the list further we found that there are 4 locations that meet all of our criterias: Boon Lay, Punggol, Tampines, and Mountbatten

Now we have successfully narrow down list of 157 locations to 4 best locations to choose from.